In [1]:
import pandas as pd
import numpy as np

In [2]:
dg3 = pd.read_csv('C:/Master/green_tripdata_2015-03_2.csv')

In [3]:
dg4 = pd.read_csv('C:/Master/green_tripdata_2015-04_2.csv')

# Visualizamos

In [4]:
import datashader as ds
from datashader import transfer_functions as tr_fns
from datashader.colors import Greys9
Greys9_r = list(reversed(Greys9))[:2]

In [5]:
from bokeh.plotting import figure, output_notebook, show
output_notebook()

Loading BokehJS ...

In [6]:
NYC = x_range, y_range = ((-75.00, -73.0), (40.0, 41.0))

plot_width = int(750)
plot_height = int(plot_width//1.2)

In [7]:
def base_plot(tools='pan, wheel_zoom, reset', plot_width=plot_width, plot_height=plot_height, **plot_args):
    p = figure(tools=tools, plot_width=plot_width, plot_height=plot_height,
              x_range=x_range, y_range=y_range, outline_line_color=None,
              min_border=0, min_border_left=0, min_border_right=0,
              min_border_top=0, min_border_bottom=0, **plot_args)
    
    p.xgrid.grid_line_color = None
    p.ygrid.grid_line_color = None
    return p

In [8]:
ejemplo = dg3.sample(n=15000)
p = base_plot()
options = dict(line_color=None, fill_color='blue', size=5)

p.circle(x=ejemplo['Pickup_longitude'], y=ejemplo['Pickup_latitude'], **options)
show(p)

In [9]:
ejemplo = dg4.sample(n=15000)
p = base_plot()
options = dict(line_color=None, fill_color='red', size=5)

p.circle(x=ejemplo['Dropoff_longitude'], y=ejemplo['Dropoff_latitude'], **options)
show(p)

In [10]:
ejemplo = dg4.sample(n=15000)
p = base_plot()
options = dict(line_color=None, fill_color='green', size=5)

p.circle(x=ejemplo['Pickup_longitude'], y=ejemplo['Pickup_latitude'], **options)
show(p)

In [11]:
ejemplo = dg4.sample(n=15000)
p = base_plot()
options = dict(line_color=None, fill_color='yellow', size=5)

p.circle(x=ejemplo['Dropoff_longitude'], y=ejemplo['Dropoff_latitude'], **options)
show(p)

# Visualización con HeatMap

In [12]:
from datashader.bokeh_ext import InteractiveImage
from functools import partial
from datashader.utils import export_image
from datashader.colors import colormap_select, Greys9, Hot, viridis, inferno
from IPython.core.display import HTML, display

background = "black"
export = partial(export_image, export_path="export", background=background)
cm = partial(colormap_select, reverse=(background=="black"))

In [13]:
def create_image(x_range, y_range, w=plot_width, h=plot_height):
    cvs = ds.Canvas(plot_width=w, plot_height=h, x_range=x_range, y_range=y_range)
    agg = cvs.points(dg3, 'Dropoff_longitude', 'Dropoff_latitude', ds.count('Passenger_count'))
    img = tr_fns.shade(agg, cmap=Hot, how='eq_hist')
    return tr_fns.dynspread(img, threshold=0.5, max_px=4)

p = base_plot(background_fill_color=background)
export(create_image(*NYC), "NYCABs")
InteractiveImage(p, create_image)

In [14]:
def create_image(x_range, y_range, w=plot_width, h=plot_height):
    cvs = ds.Canvas(plot_width=w, plot_height=h, x_range=x_range, y_range=y_range)
    agg = cvs.points(dg3, 'Pickup_longitude', 'Pickup_latitude', ds.count('Passenger_count'))
    img = tr_fns.shade(agg, cmap=Hot, how='eq_hist')
    return tr_fns.dynspread(img, threshold=0.5, max_px=4)

p = base_plot(background_fill_color=background)
export(create_image(*NYC), "NYCABs_Recoger")
InteractiveImage(p, create_image)

In [15]:
def merged_images(x_range, y_range, w=plot_width, h=plot_height, how='log'):
    cvs = ds.Canvas(plot_width=w, plot_height=h, x_range=x_range, y_range=y_range)
    picks = cvs.points(ejemplo, 'Pickup_longitude', 'Pickup_latitude', ds.count('Passenger_count'))
    drops = cvs.points(ejemplo, 'Dropoff_longitude', 'Dropoff_latitude', ds.count('Passenger_count'))
    more_drops = tr_fns.shade(drops.where(drops > picks), cmap=["darkblue", 'cornflowerblue'], how=how)
    more_picks = tr_fns.shade(drops.where(picks > drops), cmap=["darkred", 'orangered'], how=how)
    img = tr_fns.stack(more_picks, more_drops)
    return tr_fns.dynspread(img, threshold=0.3, max_px=4)

ejemplo = dg3.sample(1)
p = base_plot(background_fill_color=background)
export(merged_images(*NYC), "NYCABs_Recogida_Dejar")
InteractiveImage(p, merged_images)

MemoryError: 

Indicar que no vemos diferencias entre meses 03 y 04, observamos que hay diferencias entre zonas de recogida y dejar pasaje, este tipo de taxis, no puede recoger pasajes en la zona de bajo Manhattan, central park hasta la zona de la bolsa.

Observamos que la zona de recogida preferida son los barrios mas cercanos a Manhattan, con una fuerte presencia.

Observamos que este tipo de taxis no recoge pasaje en los aeropuertos, tanto JFK, la Guardia y New Yersey.

Hemos observado que usando la libreria datashader se realiza una buena visualización de mapa de calor, realizando una cartografia muy buena del terreno, con fuerte luz en las zonas de mas influencia, es una buena libreria a tener presente para datos con coordenadas de geolocalización.